In [1]:
import glob
import os
import numpy as np
import pandas as pd
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import LabelEncoder
from collections import defaultdict
from itertools import product

In [2]:
np.random.seed(43)

In [3]:
# Define paths to data
folder_paths = [
    '/home/sgurau/Desktop/output/functional_connectivity/AD/sub-*',
    '/home/sgurau/Desktop/output/functional_connectivity/CN/sub-*'
]

In [4]:
# Create labels for data
labels_string = []
data_matrices = []  # List to store individual correlation matrices
for folder_path in folder_paths:
    if 'AD' in folder_path:
        label = 'AD'
    elif 'CN' in folder_path:
        label = 'CN'
    
    data_files = glob.glob(os.path.join(folder_path, '*.txt'))  
    for data_file in data_files:
        # Load correlation matrix from data_file
        correlation_matrix = np.loadtxt(data_file)
        data_matrices.append(correlation_matrix)
        labels_string.append(label)

In [5]:
encoder = LabelEncoder()
labels = encoder.fit_transform(labels_string)

In [6]:
# Load the geodesic distance matrix 
geodesic_distances_file = geodesic_distances_file = '/home/sgurau/Desktop/geodesic_distances.csv'
geodesic_distances = pd.read_csv(geodesic_distances_file, header=None).values

In [7]:
# Define hyperparameter ranges
gamma_values = np.arange(10000, 1000000, 5000).tolist()
beta_values = np.arange(0.1, 2, 0.5).tolist()
C_values = np.arange(1, 100, 5).tolist()

In [8]:

# Define the number of folds for cross-validation
kfold = 5

In [9]:
# Stratification into folds
unique_labels, label_counts = np.unique(labels, return_counts=True)
folds = defaultdict(list)

In [10]:
min_sizes = {label: count // kfold for label, count in zip(unique_labels, label_counts)}
remainders = {label: count % kfold for label, count in zip(unique_labels, label_counts)}

In [11]:
for label in unique_labels:
    label_indices = np.where(labels == label)[0]
    np.random.shuffle(label_indices)
    current_fold = 0
    for index in label_indices:
        folds[current_fold].append(index)
        if len(folds[current_fold]) >= min_sizes[label] + (current_fold < remainders[label]):
            current_fold = (current_fold + 1) % kfold
           
for fold in folds:
    folds[fold] = np.array(folds[fold])

In [12]:
# Create train and test indices for each fold
train_indices_all_folds = []
test_indices_all_folds = []

In [13]:
for fold in range(kfold):
    test_indices = folds[fold]
    train_indices = np.hstack([folds[f] for f in range(kfold) if f != fold])
    train_indices_all_folds.append(train_indices)
    test_indices_all_folds.append(test_indices)

In [14]:
# Perform cross-validation
accuracy_values = []

In [15]:
# Initialize a dictionary to store the DataFrames for each fold
fold_results_dfs = {}

In [16]:
for fold in range(kfold):
    train_indices = train_indices_all_folds[fold]
    test_indices = test_indices_all_folds[fold]
    for gamma in gamma_values:
            for beta in beta_values:
                precomputed_kernel_matrix = beta * np.exp(-geodesic_distances**2 / gamma)
        
                # Regularize the kernel matrix
                # precomputed_kernel_matrix += 5e-4 * np.eye(len(geodesic_distances))        
        
                for C in C_values:    
                    classifier = SVC(kernel='precomputed', C=C) # class_weight='balanced'
                    classifier.fit(precomputed_kernel_matrix[train_indices][:, train_indices], labels[train_indices])
                    predicted_labels = classifier.predict(precomputed_kernel_matrix[test_indices][:, train_indices])
                    accuracy = accuracy_score(labels[test_indices], predicted_labels)
                    accuracy_values.append(accuracy)
                    print(f"Fold={fold}, Gamma={gamma}, Beta={beta}, C={C}, Accuracy: {accuracy:.2f}")
            
                    # Create the DataFrame and store it in the fold_results_dfs dictionary
                    fold_results_dfs[fold, gamma, beta, C] = pd.DataFrame({
                        'test_indices': test_indices,
                        'test_labels': labels[test_indices],
                        'predicted_labels': predicted_labels
                        })

Fold=0, Gamma=10000, Beta=0.1, C=1, Accuracy: 0.61
Fold=0, Gamma=10000, Beta=0.1, C=6, Accuracy: 0.61
Fold=0, Gamma=10000, Beta=0.1, C=11, Accuracy: 0.50
Fold=0, Gamma=10000, Beta=0.1, C=16, Accuracy: 0.44
Fold=0, Gamma=10000, Beta=0.1, C=21, Accuracy: 0.39
Fold=0, Gamma=10000, Beta=0.1, C=26, Accuracy: 0.39
Fold=0, Gamma=10000, Beta=0.1, C=31, Accuracy: 0.28
Fold=0, Gamma=10000, Beta=0.1, C=36, Accuracy: 0.22
Fold=0, Gamma=10000, Beta=0.1, C=41, Accuracy: 0.22
Fold=0, Gamma=10000, Beta=0.1, C=46, Accuracy: 0.22
Fold=0, Gamma=10000, Beta=0.1, C=51, Accuracy: 0.22
Fold=0, Gamma=10000, Beta=0.1, C=56, Accuracy: 0.22
Fold=0, Gamma=10000, Beta=0.1, C=61, Accuracy: 0.22
Fold=0, Gamma=10000, Beta=0.1, C=66, Accuracy: 0.22
Fold=0, Gamma=10000, Beta=0.1, C=71, Accuracy: 0.22
Fold=0, Gamma=10000, Beta=0.1, C=76, Accuracy: 0.22
Fold=0, Gamma=10000, Beta=0.1, C=81, Accuracy: 0.22
Fold=0, Gamma=10000, Beta=0.1, C=86, Accuracy: 0.22
Fold=0, Gamma=10000, Beta=0.1, C=91, Accuracy: 0.22
Fold=0, Gamma=

Fold=0, Gamma=35000, Beta=0.6, C=71, Accuracy: 0.22
Fold=0, Gamma=35000, Beta=0.6, C=76, Accuracy: 0.22
Fold=0, Gamma=35000, Beta=0.6, C=81, Accuracy: 0.22
Fold=0, Gamma=35000, Beta=0.6, C=86, Accuracy: 0.22
Fold=0, Gamma=35000, Beta=0.6, C=91, Accuracy: 0.22
Fold=0, Gamma=35000, Beta=0.6, C=96, Accuracy: 0.22
Fold=0, Gamma=35000, Beta=1.1, C=1, Accuracy: 0.61
Fold=0, Gamma=35000, Beta=1.1, C=6, Accuracy: 0.39
Fold=0, Gamma=35000, Beta=1.1, C=11, Accuracy: 0.22
Fold=0, Gamma=35000, Beta=1.1, C=16, Accuracy: 0.22
Fold=0, Gamma=35000, Beta=1.1, C=21, Accuracy: 0.22
Fold=0, Gamma=35000, Beta=1.1, C=26, Accuracy: 0.22
Fold=0, Gamma=35000, Beta=1.1, C=31, Accuracy: 0.22
Fold=0, Gamma=35000, Beta=1.1, C=36, Accuracy: 0.22
Fold=0, Gamma=35000, Beta=1.1, C=41, Accuracy: 0.22
Fold=0, Gamma=35000, Beta=1.1, C=46, Accuracy: 0.22
Fold=0, Gamma=35000, Beta=1.1, C=51, Accuracy: 0.22
Fold=0, Gamma=35000, Beta=1.1, C=56, Accuracy: 0.22
Fold=0, Gamma=35000, Beta=1.1, C=61, Accuracy: 0.22
Fold=0, Gamma=

Fold=0, Gamma=65000, Beta=0.6, C=21, Accuracy: 0.28
Fold=0, Gamma=65000, Beta=0.6, C=26, Accuracy: 0.28
Fold=0, Gamma=65000, Beta=0.6, C=31, Accuracy: 0.22
Fold=0, Gamma=65000, Beta=0.6, C=36, Accuracy: 0.22
Fold=0, Gamma=65000, Beta=0.6, C=41, Accuracy: 0.22
Fold=0, Gamma=65000, Beta=0.6, C=46, Accuracy: 0.22
Fold=0, Gamma=65000, Beta=0.6, C=51, Accuracy: 0.22
Fold=0, Gamma=65000, Beta=0.6, C=56, Accuracy: 0.22
Fold=0, Gamma=65000, Beta=0.6, C=61, Accuracy: 0.22
Fold=0, Gamma=65000, Beta=0.6, C=66, Accuracy: 0.22
Fold=0, Gamma=65000, Beta=0.6, C=71, Accuracy: 0.22
Fold=0, Gamma=65000, Beta=0.6, C=76, Accuracy: 0.22
Fold=0, Gamma=65000, Beta=0.6, C=81, Accuracy: 0.22
Fold=0, Gamma=65000, Beta=0.6, C=86, Accuracy: 0.22
Fold=0, Gamma=65000, Beta=0.6, C=91, Accuracy: 0.22
Fold=0, Gamma=65000, Beta=0.6, C=96, Accuracy: 0.22
Fold=0, Gamma=65000, Beta=1.1, C=1, Accuracy: 0.61
Fold=0, Gamma=65000, Beta=1.1, C=6, Accuracy: 0.44
Fold=0, Gamma=65000, Beta=1.1, C=11, Accuracy: 0.33
Fold=0, Gamma=

Fold=0, Gamma=95000, Beta=0.6, C=26, Accuracy: 0.39
Fold=0, Gamma=95000, Beta=0.6, C=31, Accuracy: 0.28
Fold=0, Gamma=95000, Beta=0.6, C=36, Accuracy: 0.28
Fold=0, Gamma=95000, Beta=0.6, C=41, Accuracy: 0.28
Fold=0, Gamma=95000, Beta=0.6, C=46, Accuracy: 0.22
Fold=0, Gamma=95000, Beta=0.6, C=51, Accuracy: 0.22
Fold=0, Gamma=95000, Beta=0.6, C=56, Accuracy: 0.22
Fold=0, Gamma=95000, Beta=0.6, C=61, Accuracy: 0.22
Fold=0, Gamma=95000, Beta=0.6, C=66, Accuracy: 0.22
Fold=0, Gamma=95000, Beta=0.6, C=71, Accuracy: 0.22
Fold=0, Gamma=95000, Beta=0.6, C=76, Accuracy: 0.22
Fold=0, Gamma=95000, Beta=0.6, C=81, Accuracy: 0.22
Fold=0, Gamma=95000, Beta=0.6, C=86, Accuracy: 0.22
Fold=0, Gamma=95000, Beta=0.6, C=91, Accuracy: 0.22
Fold=0, Gamma=95000, Beta=0.6, C=96, Accuracy: 0.22
Fold=0, Gamma=95000, Beta=1.1, C=1, Accuracy: 0.61
Fold=0, Gamma=95000, Beta=1.1, C=6, Accuracy: 0.44
Fold=0, Gamma=95000, Beta=1.1, C=11, Accuracy: 0.39
Fold=0, Gamma=95000, Beta=1.1, C=16, Accuracy: 0.33
Fold=0, Gamma=

Fold=0, Gamma=120000, Beta=1.6, C=51, Accuracy: 0.22
Fold=0, Gamma=120000, Beta=1.6, C=56, Accuracy: 0.22
Fold=0, Gamma=120000, Beta=1.6, C=61, Accuracy: 0.22
Fold=0, Gamma=120000, Beta=1.6, C=66, Accuracy: 0.22
Fold=0, Gamma=120000, Beta=1.6, C=71, Accuracy: 0.22
Fold=0, Gamma=120000, Beta=1.6, C=76, Accuracy: 0.22
Fold=0, Gamma=120000, Beta=1.6, C=81, Accuracy: 0.22
Fold=0, Gamma=120000, Beta=1.6, C=86, Accuracy: 0.22
Fold=0, Gamma=120000, Beta=1.6, C=91, Accuracy: 0.22
Fold=0, Gamma=120000, Beta=1.6, C=96, Accuracy: 0.22
Fold=0, Gamma=125000, Beta=0.1, C=1, Accuracy: 0.61
Fold=0, Gamma=125000, Beta=0.1, C=6, Accuracy: 0.61
Fold=0, Gamma=125000, Beta=0.1, C=11, Accuracy: 0.61
Fold=0, Gamma=125000, Beta=0.1, C=16, Accuracy: 0.61
Fold=0, Gamma=125000, Beta=0.1, C=21, Accuracy: 0.61
Fold=0, Gamma=125000, Beta=0.1, C=26, Accuracy: 0.61
Fold=0, Gamma=125000, Beta=0.1, C=31, Accuracy: 0.61
Fold=0, Gamma=125000, Beta=0.1, C=36, Accuracy: 0.61
Fold=0, Gamma=125000, Beta=0.1, C=41, Accuracy: 

...

Fold=4, Gamma=850000, Beta=0.1, C=66, Accuracy: 0.62
Fold=4, Gamma=850000, Beta=0.1, C=71, Accuracy: 0.62
Fold=4, Gamma=850000, Beta=0.1, C=76, Accuracy: 0.62
Fold=4, Gamma=850000, Beta=0.1, C=81, Accuracy: 0.62
Fold=4, Gamma=850000, Beta=0.1, C=86, Accuracy: 0.62
Fold=4, Gamma=850000, Beta=0.1, C=91, Accuracy: 0.62
Fold=4, Gamma=850000, Beta=0.1, C=96, Accuracy: 0.62
Fold=4, Gamma=850000, Beta=0.6, C=1, Accuracy: 0.62
Fold=4, Gamma=850000, Beta=0.6, C=6, Accuracy: 0.62
Fold=4, Gamma=850000, Beta=0.6, C=11, Accuracy: 0.62
Fold=4, Gamma=850000, Beta=0.6, C=16, Accuracy: 0.62
Fold=4, Gamma=850000, Beta=0.6, C=21, Accuracy: 0.62
Fold=4, Gamma=850000, Beta=0.6, C=26, Accuracy: 0.62
Fold=4, Gamma=850000, Beta=0.6, C=31, Accuracy: 0.62
Fold=4, Gamma=850000, Beta=0.6, C=36, Accuracy: 0.56
Fold=4, Gamma=850000, Beta=0.6, C=41, Accuracy: 0.56
Fold=4, Gamma=850000, Beta=0.6, C=46, Accuracy: 0.56
Fold=4, Gamma=850000, Beta=0.6, C=51, Accuracy: 0.56
Fold=4, Gamma=850000, Beta=0.6, C=56, Accuracy: 

Fold=4, Gamma=880000, Beta=0.6, C=6, Accuracy: 0.62
Fold=4, Gamma=880000, Beta=0.6, C=11, Accuracy: 0.62
Fold=4, Gamma=880000, Beta=0.6, C=16, Accuracy: 0.62
Fold=4, Gamma=880000, Beta=0.6, C=21, Accuracy: 0.62
Fold=4, Gamma=880000, Beta=0.6, C=26, Accuracy: 0.62
Fold=4, Gamma=880000, Beta=0.6, C=31, Accuracy: 0.62
Fold=4, Gamma=880000, Beta=0.6, C=36, Accuracy: 0.56
Fold=4, Gamma=880000, Beta=0.6, C=41, Accuracy: 0.56
Fold=4, Gamma=880000, Beta=0.6, C=46, Accuracy: 0.56
Fold=4, Gamma=880000, Beta=0.6, C=51, Accuracy: 0.56
Fold=4, Gamma=880000, Beta=0.6, C=56, Accuracy: 0.56
Fold=4, Gamma=880000, Beta=0.6, C=61, Accuracy: 0.56
Fold=4, Gamma=880000, Beta=0.6, C=66, Accuracy: 0.56
Fold=4, Gamma=880000, Beta=0.6, C=71, Accuracy: 0.56
Fold=4, Gamma=880000, Beta=0.6, C=76, Accuracy: 0.56
Fold=4, Gamma=880000, Beta=0.6, C=81, Accuracy: 0.50
Fold=4, Gamma=880000, Beta=0.6, C=86, Accuracy: 0.50
Fold=4, Gamma=880000, Beta=0.6, C=91, Accuracy: 0.50
Fold=4, Gamma=880000, Beta=0.6, C=96, Accuracy:

Fold=4, Gamma=910000, Beta=1.1, C=6, Accuracy: 0.62
Fold=4, Gamma=910000, Beta=1.1, C=11, Accuracy: 0.62
Fold=4, Gamma=910000, Beta=1.1, C=16, Accuracy: 0.62
Fold=4, Gamma=910000, Beta=1.1, C=21, Accuracy: 0.56
Fold=4, Gamma=910000, Beta=1.1, C=26, Accuracy: 0.56
Fold=4, Gamma=910000, Beta=1.1, C=31, Accuracy: 0.56
Fold=4, Gamma=910000, Beta=1.1, C=36, Accuracy: 0.56
Fold=4, Gamma=910000, Beta=1.1, C=41, Accuracy: 0.56
Fold=4, Gamma=910000, Beta=1.1, C=46, Accuracy: 0.50
Fold=4, Gamma=910000, Beta=1.1, C=51, Accuracy: 0.50
Fold=4, Gamma=910000, Beta=1.1, C=56, Accuracy: 0.50
Fold=4, Gamma=910000, Beta=1.1, C=61, Accuracy: 0.44
Fold=4, Gamma=910000, Beta=1.1, C=66, Accuracy: 0.44
Fold=4, Gamma=910000, Beta=1.1, C=71, Accuracy: 0.44
Fold=4, Gamma=910000, Beta=1.1, C=76, Accuracy: 0.44
Fold=4, Gamma=910000, Beta=1.1, C=81, Accuracy: 0.44
Fold=4, Gamma=910000, Beta=1.1, C=86, Accuracy: 0.44
Fold=4, Gamma=910000, Beta=1.1, C=91, Accuracy: 0.44
Fold=4, Gamma=910000, Beta=1.1, C=96, Accuracy:

Fold=4, Gamma=940000, Beta=1.1, C=96, Accuracy: 0.38
Fold=4, Gamma=940000, Beta=1.6, C=1, Accuracy: 0.62
Fold=4, Gamma=940000, Beta=1.6, C=6, Accuracy: 0.62
Fold=4, Gamma=940000, Beta=1.6, C=11, Accuracy: 0.62
Fold=4, Gamma=940000, Beta=1.6, C=16, Accuracy: 0.56
Fold=4, Gamma=940000, Beta=1.6, C=21, Accuracy: 0.56
Fold=4, Gamma=940000, Beta=1.6, C=26, Accuracy: 0.56
Fold=4, Gamma=940000, Beta=1.6, C=31, Accuracy: 0.56
Fold=4, Gamma=940000, Beta=1.6, C=36, Accuracy: 0.50
Fold=4, Gamma=940000, Beta=1.6, C=41, Accuracy: 0.50
Fold=4, Gamma=940000, Beta=1.6, C=46, Accuracy: 0.44
Fold=4, Gamma=940000, Beta=1.6, C=51, Accuracy: 0.44
Fold=4, Gamma=940000, Beta=1.6, C=56, Accuracy: 0.44
Fold=4, Gamma=940000, Beta=1.6, C=61, Accuracy: 0.44
Fold=4, Gamma=940000, Beta=1.6, C=66, Accuracy: 0.38
Fold=4, Gamma=940000, Beta=1.6, C=71, Accuracy: 0.38
Fold=4, Gamma=940000, Beta=1.6, C=76, Accuracy: 0.38
Fold=4, Gamma=940000, Beta=1.6, C=81, Accuracy: 0.38
Fold=4, Gamma=940000, Beta=1.6, C=86, Accuracy: 

Fold=4, Gamma=970000, Beta=1.6, C=96, Accuracy: 0.38
Fold=4, Gamma=975000, Beta=0.1, C=1, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=6, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=11, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=16, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=21, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=26, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=31, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=36, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=41, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=46, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=51, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=56, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=61, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=66, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=71, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=76, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=81, Accuracy: 0.62
Fold=4, Gamma=975000, Beta=0.1, C=86, Accuracy: 

In [17]:
# Reshape the accuracy values for analysis
accuracy_values = np.array(accuracy_values).reshape(kfold, len(gamma_values), len(beta_values), -1)

In [18]:
# Calculate the average accuracy and standard deviation across folds
average_accuracy = np.mean(accuracy_values, axis=0)
std_dev = np.std(accuracy_values, axis=0)

In [19]:
# Combine gamma, beta, and C values for results
parameter_combinations = [(g, b, c) for g, b, c in product(gamma_values, beta_values, C_values)]
results_df = pd.DataFrame({
    'Gamma': [comb[0] for comb in parameter_combinations],
    'Beta': [comb[1] for comb in parameter_combinations],
    'C': [comb[2] for comb in parameter_combinations],
    'Average Accuracy': average_accuracy.flatten(),
    'Standard Deviation': std_dev.flatten()
})

In [20]:
# Find the best combination of parameters
best_index = results_df['Average Accuracy'].idxmax()
best_parameters = results_df.loc[best_index]

In [21]:
print("Best Parameters:")
print(best_parameters)

Best Parameters:
Gamma                 10000.000000
Beta                      0.100000
C                         1.000000
Average Accuracy          0.604739
Standard Deviation        0.014398
Name: 0, dtype: float64


In [22]:

# Calculate label distribution in the entire dataset
total_label_distribution = {label: np.sum(labels == label) for label in unique_labels}

In [23]:
# Initialize a dictionary to hold the label distribution for each fold
fold_label_distributions = {fold: {label: 0 for label in unique_labels} for fold in range(kfold)}

In [24]:
# Calculate label distribution for each fold
for fold in range(kfold):
    fold_labels = labels[test_indices_all_folds[fold]]
    for label in unique_labels:
        fold_label_distributions[fold][label] = np.sum(fold_labels == label)

In [25]:
# Print distributions to compare them
print("Label distribution in the entire dataset:")
print(total_label_distribution)

Label distribution in the entire dataset:
{0: 34, 1: 52}


In [26]:
print("\nLabel distribution in each fold:")
for fold in range(kfold):
    print(f"Fold {fold}: {fold_label_distributions[fold]}")


Label distribution in each fold:
Fold 0: {0: 7, 1: 11}
Fold 1: {0: 7, 1: 11}
Fold 2: {0: 7, 1: 10}
Fold 3: {0: 7, 1: 10}
Fold 4: {0: 6, 1: 10}


In [27]:
# Calculate the expected distribution in each fold (as a proportion)
expected_distribution = {label: count / len(labels) for label, count in total_label_distribution.items()}

In [28]:
# Compare the fold distributions to the expected distribution
print("\nExpected label distribution (as proportions):")
print(expected_distribution)


Expected label distribution (as proportions):
{0: 0.3953488372093023, 1: 0.6046511627906976}


In [29]:
# Check if the folds are approximately equal to the expected distribution
for fold in range(kfold):
    fold_distribution_proportion = {
        label: fold_label_distributions[fold][label] / sum(fold_label_distributions[fold].values()) 
        for label in fold_label_distributions[fold]
    }
    print(f"Fold {fold} distribution as a proportion of total for each label:")
    print(fold_distribution_proportion)
    
# Dataframes to show train and test indices for each fold
# train_indices_df = pd.DataFrame(train_indices_all_folds, index=[f'Fold {i+1}' for i in range(kfold)])
# test_indices_df = pd.DataFrame(test_indices_all_folds, index=[f'Fold {i+1}' for i in range(kfold)])

Fold 0 distribution as a proportion of total for each label:
{0: 0.3888888888888889, 1: 0.6111111111111112}
Fold 1 distribution as a proportion of total for each label:
{0: 0.3888888888888889, 1: 0.6111111111111112}
Fold 2 distribution as a proportion of total for each label:
{0: 0.4117647058823529, 1: 0.5882352941176471}
Fold 3 distribution as a proportion of total for each label:
{0: 0.4117647058823529, 1: 0.5882352941176471}
Fold 4 distribution as a proportion of total for each label:
{0: 0.375, 1: 0.625}
